<a href="https://colab.research.google.com/github/jballesterosc/hacking-civico/blob/master/proyecto/contratos_covid_cdmx.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Análisis de contratos adjudicados para atender la situación del COVID-19 en la Ciudad de México**
------
##### **Autor**
- [Jay Ballesteros](https://twitter.com/jballesterosc_)

##### **Fuente**
- [*Contratos adjudicados por COVID-19 - Datos Abiertos de la Ciudad de México*](https://datos.cdmx.gob.mx/explore/dataset/contratos-adjudicados-covid19/information/?dataChart=eyJxdWVyaWVzIjpbeyJjaGFydHMiOlt7InR5cGUiOiJiYXIiLCJmdW5jIjoiU1VNIiwieUF4aXMiOiJtb250b19jb250cmF0b19taW5pbW8iLCJzY2llbnRpZmljRGlzcGxheSI6dHJ1ZSwiY29sb3IiOiJyYW5nZS1BY2NlbnQifV0sInhBeGlzIjoiZmVjaGFfYWRqdWRpY2FjaW9uIiwibWF4cG9pbnRzIjoiIiwidGltZXNjYWxlIjoiZGF5Iiwic29ydCI6IiIsImNvbmZpZyI6eyJkYXRhc2V0IjoiY29udHJhdG9zLWFkanVkaWNhZG9zLWNvdmlkMTkiLCJvcHRpb25zIjp7fX0sInNlcmllc0JyZWFrZG93biI6Im1vbnRvX2NvbnRyYXRvX21pbmltbyJ9XSwiZGlzcGxheUxlZ2VuZCI6dHJ1ZSwiYWxpZ25Nb250aCI6dHJ1ZSwidGltZXNjYWxlIjoiIn0%3D&calendarview=month)


--------------------






In [ ]:
import altair as alt
import seaborn as sns
import pandas as pd
import statistics

In [ ]:
#Source Contratos adjudicados por COVID-19 — Datos CDMX

data = 'https://datos.cdmx.gob.mx/explore/dataset/contratos-adjudicados-covid19/download/?format=csv&timezone=America/Mexico_City&lang=es&use_labels_for_header=true&csv_separator=%2C'

df = pd.read_csv(data, encoding='utf-8')

# **Exploración de los datos**
-----------

In [ ]:
df.columns 

Index(['id', 'ente_id', 'ente_nombre', 'tipo_formalización', 'no_contrato',
       'objeto_contrato', 'justificacion_covid19', 'tipo_contratación',
       'tipo_contrato', 'monto_contrato_minimo', 'monto_contrato',
       'fecha_adjudicacion', 'fecha_inicio_contrato', 'fecha_fin_contrato',
       'modalidad_contratacion', 'proveedor_rfc', 'proveedor_nombre',
       'no_cotizaciones', 'capitulo', 'partida', 'no_cabms_contrato',
       'cabms_descripcion', 'unidad_medida', 'marca', 'cantidad minima',
       'cantidad_maxima', 'es_consolidado', 'estatus_contrato',
       'fecha_validación'],
      dtype='object')

In [ ]:
# ¿Cuántas filas y cuántas columnas tenemos?
print('Número de filas: {}'.format(df.shape[0]))
print('Número de columnas: {}'.format(df.shape[1]))

Número de filas: 781
Número de columnas: 29


In [ ]:
# ¿Qué formato tienen los valores de las columnas.
df.dtypes

id                          int64
ente_id                    object
ente_nombre                object
tipo_formalización         object
no_contrato                object
objeto_contrato            object
justificacion_covid19      object
tipo_contratación          object
tipo_contrato              object
monto_contrato_minimo     float64
monto_contrato             object
fecha_adjudicacion         object
fecha_inicio_contrato      object
fecha_fin_contrato         object
modalidad_contratacion     object
proveedor_rfc              object
proveedor_nombre           object
no_cotizaciones             int64
capitulo                   object
partida                    object
no_cabms_contrato         float64
cabms_descripcion          object
unidad_medida              object
marca                      object
cantidad minima            object
cantidad_maxima            object
es_consolidado            float64
estatus_contrato           object
fecha_validación           object
dtype: object

In [ ]:
# Cambiamos el formato de las columnas que tenga como título `fecha`.

def cast_datetime_cols(data):
    timestamp_cols = [col for col in data.columns if "fecha" in col]
    data[timestamp_cols] = data[timestamp_cols].apply(lambda date_col: pd.to_datetime(date_col, errors="coerce"), axis=0)
    return data

df = cast_datetime_cols(df)

# Con este cambiamos el monto_contrato a objeto numérico, y sustituimos la coma de los decimales por un punto. 
df['monto_contrato'] = pd.to_numeric(df['monto_contrato'].str.replace(',', '.'))


In [ ]:
#Verfificamos si cambio el formato de fecha en las columnas
df.dtypes

id                                 int64
ente_id                           object
ente_nombre                       object
tipo_formalización                object
no_contrato                       object
objeto_contrato                   object
justificacion_covid19             object
tipo_contratación                 object
tipo_contrato                     object
monto_contrato_minimo            float64
monto_contrato                   float64
fecha_adjudicacion        datetime64[ns]
fecha_inicio_contrato     datetime64[ns]
fecha_fin_contrato        datetime64[ns]
modalidad_contratacion            object
proveedor_rfc                     object
proveedor_nombre                  object
no_cotizaciones                    int64
capitulo                          object
partida                           object
no_cabms_contrato                float64
cabms_descripcion                 object
unidad_medida                     object
marca                             object
cantidad minima 

In [ ]:
df.head()

id ente_id  ... estatus_contrato fecha_validación
0  31712  26C001  ...          VIGENTE       2020-09-14
1  31537  11CD03  ...          VENCIDO       2020-08-24
2  32318  08PDII  ...          VENCIDO       2020-08-10
3  34987  34C001  ...          VENCIDO       2020-08-24
4  38419  11C001  ...          VIGENTE       2020-08-26

[5 rows x 29 columns]

In [ ]:
# Valores por columna: cardinalidad
categorical = df.select_dtypes(include=['object', 'bool', 'category', 'datetime64[ns]'])

for col in categorical.columns:
  print('Valores únicos en "{}": {}'.format(col,categorical[col].nunique()))

Valores únicos en "ente_id": 68
Valores únicos en "ente_nombre": 68
Valores únicos en "tipo_formalización": 2
Valores únicos en "no_contrato": 298
Valores únicos en "objeto_contrato": 264
Valores únicos en "justificacion_covid19": 166
Valores únicos en "tipo_contratación": 3
Valores únicos en "tipo_contrato": 3
Valores únicos en "fecha_adjudicacion": 81
Valores únicos en "fecha_inicio_contrato": 86
Valores únicos en "fecha_fin_contrato": 72
Valores únicos en "modalidad_contratacion": 7
Valores únicos en "proveedor_rfc": 199
Valores únicos en "proveedor_nombre": 217
Valores únicos en "capitulo": 5
Valores únicos en "partida": 81
Valores únicos en "cabms_descripcion": 141
Valores únicos en "unidad_medida": 58
Valores únicos en "marca": 73
Valores únicos en "cantidad minima": 294
Valores únicos en "cantidad_maxima": 298
Valores únicos en "estatus_contrato": 3
Valores únicos en "fecha_validación": 46


In [ ]:
# Unicidad - proporción de valores únicos por columna
total = df.shape[0]
for col in categorical.columns:
  print('Porcentaje de valores únicos en "{}": {}%'.format(col,round(categorical[col].nunique()/total*100,2)))

Porcentaje de valores únicos en "ente_id": 8.71%
Porcentaje de valores únicos en "ente_nombre": 8.71%
Porcentaje de valores únicos en "tipo_formalización": 0.26%
Porcentaje de valores únicos en "no_contrato": 38.16%
Porcentaje de valores únicos en "objeto_contrato": 33.8%
Porcentaje de valores únicos en "justificacion_covid19": 21.25%
Porcentaje de valores únicos en "tipo_contratación": 0.38%
Porcentaje de valores únicos en "tipo_contrato": 0.38%
Porcentaje de valores únicos en "fecha_adjudicacion": 10.37%
Porcentaje de valores únicos en "fecha_inicio_contrato": 11.01%
Porcentaje de valores únicos en "fecha_fin_contrato": 9.22%
Porcentaje de valores únicos en "modalidad_contratacion": 0.9%
Porcentaje de valores únicos en "proveedor_rfc": 25.48%
Porcentaje de valores únicos en "proveedor_nombre": 27.78%
Porcentaje de valores únicos en "capitulo": 0.64%
Porcentaje de valores únicos en "partida": 10.37%
Porcentaje de valores únicos en "cabms_descripcion": 18.05%
Porcentaje de valores únic

In [ ]:
# Moda - valor que más se repite en cada columna excepto los indicadores únicos
for col in categorical.drop(columns='ente_id').columns:
  print('Valor más popular en "{}": {}'.format(col, statistics.mode(categorical[col])))

Valor más popular en "ente_nombre": SECRETARÍA DE SALUD
Valor más popular en "tipo_formalización": CONTRATO-TIPO
Valor más popular en "no_contrato": DEABS-01-2020
Valor más popular en "objeto_contrato": ADQUISICIÓN DE GEL ANTIBACTERIAL
Valor más popular en "justificacion_covid19": A FIN DE ATENDER LA COMPRA CONSOLIDADA DE CONFORMIDAD  A LO ESTABLECIDO EN EL ARTÍCULO 57 Y 63 DE LA LEY DE ADQUISICIONES PARA EL DISTRITO FEDERAL, Y TODA VEZ QUE, A CONSECUENCIA DE LA DECLARATORIA DE PANDEMIA QUE REALIZÓ LA ORGANIZACIÓN MUNDIAL DE LA SALUD (OMS) CON RELACIÓN AL VIRUS COVID-19 EL PASADO 11 DE MARZO DEL AÑO EN CURSO.
Valor más popular en "tipo_contratación": ADQUISICIÓN DE BIENES
Valor más popular en "tipo_contrato": ABIERTO/MONTO
Valor más popular en "fecha_adjudicacion": 2020-03-27 00:00:00
Valor más popular en "fecha_inicio_contrato": 2020-03-27 00:00:00
Valor más popular en "fecha_fin_contrato": 2020-12-31 00:00:00
Valor más popular en "modalidad_contratacion": ADJUDICACIÓN DIRECTA / ARTÍC

### **Proveedores**

> Nombre o razón social del proveedor adjudicado con el contrato.


In [ ]:
df.proveedor_nombre.value_counts()

COMERCIALIZADORA TECNO-HOSPITALARIA SA DE CV                         53
CLENPROCESS SA DE CV                                                 52
OPORTUNIDADES RAL, S.A. DE C.V.                                      41
NUBE MÉDICA, S.A.P.I. DE C.V.                                        36
CORPORATIVO PROMED S.A. DE C.V.                                      34
                                                                     ..
CORPORACION AMBIENTAL URBANA SA DE CV                                 1
COMERCIALIZADORA Y DISTRIBUIDORA LOGOS SA DE CV                       1
CODELMEX SA DE CV                                                     1
GENERACION DE RIQUEZA POR ARTICULOS GRANDIOSOS MEXICANOS SA DE CV     1
ADRIANA  GUILLERMINA  BUSSEY SARMENTO                                 1
Name: proveedor_nombre, Length: 217, dtype: int64

In [ ]:
#Porcentajes
counts = df.proveedor_nombre.value_counts()
percent = df.proveedor_nombre.value_counts(normalize=True)
percent100 = df.proveedor_nombre.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
COMERCIALIZADORA TECNO-HOSPITALARIA SA DE CV            53  0.067862   6.8%
CLENPROCESS SA DE CV                                    52  0.066581   6.7%
OPORTUNIDADES RAL, S.A. DE C.V.                         41  0.052497   5.2%
NUBE MÉDICA, S.A.P.I. DE C.V.                           36  0.046095   4.6%
CORPORATIVO PROMED S.A. DE C.V.                         34  0.043534   4.4%
...                                                    ...       ...    ...
CORPORACION AMBIENTAL URBANA SA DE CV                    1  0.001280   0.1%
COMERCIALIZADORA Y DISTRIBUIDORA LOGOS SA DE CV          1  0.001280   0.1%
CODELMEX SA DE CV                                        1  0.001280   0.1%
GENERACION DE RIQUEZA POR ARTICULOS GRANDIOSOS ...       1  0.001280   0.1%
ADRIANA  GUILLERMINA  BUSSEY SARMENTO                    1  0.001280   0.1%

[217 rows x 3 columns]

### **Erogaciones por capítulo**

> Capítulo (s) del Clasificador por Objeto del Gasto de la Ciudad de México en el (los) que se comprometió el monto de la contratación.

In [ ]:
# Erogaciones por capítulo
df.capitulo.value_counts()

2000         715
3000          47
5000          17
2000;5000      1
4000           1
Name: capitulo, dtype: int64

In [ ]:
#Porcentajes
counts = df.capitulo.value_counts()
percent = df.capitulo.value_counts(normalize=True)
percent100 = df.capitulo.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
2000          715  0.915493  91.5%
3000           47  0.060179   6.0%
5000           17  0.021767   2.2%
2000;5000       1  0.001280   0.1%
4000            1  0.001280   0.1%

### **Fecha de adjudicación**
> Fecha en la que se adjudicó el contrato o se realizó la compra.

In [ ]:
#Adjudicaciones por fecha. Orden descendente
df.fecha_adjudicacion.value_counts()

2020-03-27    72
2020-03-13    57
2020-04-09    52
2020-04-10    41
2020-07-13    28
              ..
2020-02-28     1
2020-03-19     1
2020-05-01     1
2020-06-12     1
2020-07-30     1
Name: fecha_adjudicacion, Length: 81, dtype: int64

In [ ]:
#Porcentajes
counts = df.fecha_adjudicacion.value_counts()
percent = df.fecha_adjudicacion.value_counts(normalize=True)
percent100 = df.fecha_adjudicacion.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
2020-03-27      72  0.092190   9.2%
2020-03-13      57  0.072983   7.3%
2020-04-09      52  0.066581   6.7%
2020-04-10      41  0.052497   5.2%
2020-07-13      28  0.035851   3.6%
...            ...       ...    ...
2020-02-28       1  0.001280   0.1%
2020-03-19       1  0.001280   0.1%
2020-05-01       1  0.001280   0.1%
2020-06-12       1  0.001280   0.1%
2020-07-30       1  0.001280   0.1%

[81 rows x 3 columns]

### **Por número de contrato**

> _Número de contrato asignado por el ente público que realiza la contratación._



In [ ]:
df.no_contrato.value_counts()

DEABS-01-2020                                   53
DEABS-02-2020                                   44
DEABS-46-2020                                   22
DEABS-15-2020 (OFICIO SAF-DGRMSG-AD-19-2020)    20
DEABS-07-2020 (OFICIO SAF-DGRMSG-AD-11-2020)    19
                                                ..
AGEPSA/CP-08/2020                                1
Z 0071790                                        1
SSCDMX-DGAF-157-2020                             1
SSCDMX-DGAF-080-2020                             1
SSC/152/2020                                     1
Name: no_contrato, Length: 298, dtype: int64

In [ ]:
#Porcentajes
counts = df.no_contrato.value_counts()
percent = df.no_contrato.value_counts(normalize=True)
percent100 = df.no_contrato.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
DEABS-01-2020                                     53  0.067862   6.8%
DEABS-02-2020                                     44  0.056338   5.6%
DEABS-46-2020                                     22  0.028169   2.8%
DEABS-15-2020 (OFICIO SAF-DGRMSG-AD-19-2020)      20  0.025608   2.6%
DEABS-07-2020 (OFICIO SAF-DGRMSG-AD-11-2020)      19  0.024328   2.4%
...                                              ...       ...    ...
AGEPSA/CP-08/2020                                  1  0.001280   0.1%
Z 0071790                                          1  0.001280   0.1%
SSCDMX-DGAF-157-2020                               1  0.001280   0.1%
SSCDMX-DGAF-080-2020                               1  0.001280   0.1%
SSC/152/2020                                       1  0.001280   0.1%

[298 rows x 3 columns]

### **Por objeto de contrato**

> _Descripción de bien y/o servicio que se contrata._


In [ ]:
df.objeto_contrato.value_counts()

ADQUISICIÓN DE GEL ANTIBACTERIAL                                                                                     117
TERMÓMETRO INFRARROJO                                                                                                 44
ADQUISICIÓN DE PROTECTOR FACIAL (CARETA)                                                                              22
ADQUISICIÓN DE CUBREBOCAS DE TRES CAPAS                                                                               21
GUANTES DE LATEX, NO ESTÉRILES                                                                                        20
                                                                                                                    ... 
MATERIAL DE CURACION (GUANTES Y CUBREBOCAS 3 CAPAS) EN DIFERENTES PRESENTACIONES                                       1
ADQUISICIÓN DE TERMÓMETROS DIGITALES                                                                                   1
SERVICIO DE DESINFECCIÓN EN 481,

In [ ]:
#Porcentajes
counts = df.objeto_contrato.value_counts()
percent = df.objeto_contrato.value_counts(normalize=True)
percent100 = df.objeto_contrato.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
ADQUISICIÓN DE GEL ANTIBACTERIAL                       117  0.149808  15.0%
TERMÓMETRO INFRARROJO                                   44  0.056338   5.6%
ADQUISICIÓN DE PROTECTOR FACIAL (CARETA)                22  0.028169   2.8%
ADQUISICIÓN DE CUBREBOCAS DE TRES CAPAS                 21  0.026889   2.7%
GUANTES DE LATEX, NO ESTÉRILES                          20  0.025608   2.6%
...                                                    ...       ...    ...
MATERIAL DE CURACION (GUANTES Y CUBREBOCAS 3 CA...       1  0.001280   0.1%
ADQUISICIÓN DE TERMÓMETROS DIGITALES                     1  0.001280   0.1%
SERVICIO DE DESINFECCIÓN EN 481,824 M2 DE LOS I...       1  0.001280   0.1%
ADQUISICIÓN DE 100 CARETAS PROTECTORAS LAVABLES...       1  0.001280   0.1%
ESFIGMOMANÓMETRO ANEROIDE MÓVIL ADULTO                   1  0.001280   0.1%

[264 rows x 3 columns]

### **Por tipo de contrato**

> _Tipo de contrato, de acuerdo a la determinación de cantidades o plazos fijos los contratos podrán ser abiertos o cerrados. En los contratos abiertos se fijan cantidades mínimas y máximas de consumo y montos de contratación mínimos y máximos._


In [ ]:
df.tipo_contrato.value_counts()

ABIERTO/MONTO    409
CERRADO          366
ABIERTO/FECHA      6
Name: tipo_contrato, dtype: int64

In [ ]:
#Porcentajes
counts = df.tipo_contrato.value_counts()
percent = df.tipo_contrato.value_counts(normalize=True)
percent100 = df.tipo_contrato.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
ABIERTO/MONTO     409  0.523688  52.4%
CERRADO           366  0.468630  46.9%
ABIERTO/FECHA       6  0.007682   0.8%

### **Entes**

> _Nombre del ente público que realiza la contratación o que se adhirió al contrato consolidado formalizado por la Dirección General de Recursos Materiales y Servicios Generales._


In [ ]:
df.ente_nombre.value_counts()

SECRETARÍA DE SALUD                                                                          61
SISTEMA DE AGUAS                                                                             38
AGENCIA DE PROTECCIÓN SANITARIA                                                              35
SECRETARÍA DE SEGURIDAD CIUDADANA                                                            33
HEROICO CUERPO DE BOMBEROS                                                                   31
                                                                                             ..
FONDO PARA EL DESARROLLO ECONÓMICO Y SOCIAL                                                   1
INSTITUTO DEL DEPORTE                                                                         1
FIDEICOMISO DE PROMOCION Y DESARROLLO DEL CINE MEXICANO                                       1
FONDO DE DESARROLLO ECONÓMICO DEL DISTRITO FEDERAL                                            1
MECANISMO DE PROTECCIÓN INTEGRAL DE PERS

In [ ]:
#Porcentajes
counts = df.ente_nombre.value_counts()
percent = df.ente_nombre.value_counts(normalize=True)
percent100 = df.ente_nombre.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
SECRETARÍA DE SALUD                                     61  0.078105   7.8%
SISTEMA DE AGUAS                                        38  0.048656   4.9%
AGENCIA DE PROTECCIÓN SANITARIA                         35  0.044814   4.5%
SECRETARÍA DE SEGURIDAD CIUDADANA                       33  0.042254   4.2%
HEROICO CUERPO DE BOMBEROS                              31  0.039693   4.0%
...                                                    ...       ...    ...
FONDO PARA EL DESARROLLO ECONÓMICO Y SOCIAL              1  0.001280   0.1%
INSTITUTO DEL DEPORTE                                    1  0.001280   0.1%
FIDEICOMISO DE PROMOCION Y DESARROLLO DEL CINE ...       1  0.001280   0.1%
FONDO DE DESARROLLO ECONÓMICO DEL DISTRITO FEDERAL       1  0.001280   0.1%
MECANISMO DE PROTECCIÓN INTEGRAL DE PERSONAS DE...       1  0.001280   0.1%

[68 rows x 3 columns]

### **Tipo de contratación**

> _Tipo de contratación de acuerdo con el objeto, ya sea arrendamiento, adquisición de bienes o prestación de servicios._



In [ ]:
df.tipo_contratación.value_counts()

ADQUISICIÓN DE BIENES      734
PRESTACIÓN DE SERVICIO      43
ARRENDAMIENTO DE BIENES      4
Name: tipo_contratación, dtype: int64

In [ ]:
#Porcentajes
counts = df.tipo_contratación.value_counts()
percent = df.tipo_contratación.value_counts(normalize=True)
percent100 = df.tipo_contratación.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
ADQUISICIÓN DE BIENES       734  0.939821  94.0%
PRESTACIÓN DE SERVICIO       43  0.055058   5.5%
ARRENDAMIENTO DE BIENES       4  0.005122   0.5%

### **Número de cotizaciones por contrato**

> _Número de cotizaciones con propuestas viables, consideradas en el estudio de precios previo a la adjudicación_


In [ ]:
df.no_cotizaciones.value_counts()

4     292
3     116
5      87
6      74
2      74
1      66
7      46
13     11
8       8
12      5
9       2
Name: no_cotizaciones, dtype: int64

In [ ]:
#Porcentajes
counts = df.no_cotizaciones.value_counts()
percent = df.no_cotizaciones.value_counts(normalize=True)
percent100 = df.no_cotizaciones.value_counts(normalize=True).mul(100).round(1).astype(str) + '%'
pd.DataFrame({'counts': counts, 'per': percent, 'per100': percent100})

counts       per per100
4      292  0.373880  37.4%
3      116  0.148528  14.9%
5       87  0.111396  11.1%
6       74  0.094750   9.5%
2       74  0.094750   9.5%
1       66  0.084507   8.5%
7       46  0.058899   5.9%
13      11  0.014085   1.4%
8        8  0.010243   1.0%
12       5  0.006402   0.6%
9        2  0.002561   0.3%

# **Visualizando los datos**
--------------

In [ ]:
#Monto asignado por fecha de adjudicación

monto_fecha = alt.Chart(df).mark_line().encode(
    x = alt.X('fecha_adjudicacion:T', title = " "),
    y = alt.Y('sum(monto_contrato_minimo):Q', title = "Monto adjudicado")
).properties(
    width = 500,
    height= 500,
    title = "Monto asignado por fecha de adjudicación"
)



#Tipo de contratación por fecha de adjudicación

contratos_fecha = alt.Chart(df).mark_circle().encode(
    x = alt.X('fecha_adjudicacion:T', title = " "),
    y = alt.Y('tipo_contratación:N', title = "Tipo de contratación"),
).properties(
    width = 700,
    height= 200,
    title = "Tipo de contratación por fecha de adjudicación",
)



monto_fecha | contratos_fecha 

alt.HConcatChart(...)

In [ ]:
# Número de contratos asignados por proveedor

contratos_proveedor = alt.Chart(df).mark_bar().encode(
  x = alt.X('count:Q', title = "Número de contratos"),
  y = alt.Y('proveedor_nombre:N', sort='-x', title = "Proveedores")
).transform_aggregate(
  count='count()',
  groupby=['proveedor_nombre']
).transform_window(
  rank='rank(count)',
  sort=[alt.SortField('count', order='descending')]
).transform_filter(
  alt.datum.rank <= 20
).properties(
    width = 600,
    height= 500,
    title = "Número de contratos asignados por proveedor (Top 21)"
)



# Monto total asignado por proveedor (top 20)

monto_proveedor = alt.Chart(df).mark_bar().encode(
    x = alt.X('sum(monto_contrato_minimo):Q', title = "Monto adjudicado"),
    y = alt.Y('proveedor_nombre:N', sort='-x', title = "Proveedores")
).transform_window(
  rank='rank(monto_contrato_minimo))',
  sort=[alt.SortField('monto_contrato_minimo', order='descending')]
).transform_filter(
  alt.datum.rank <= 21
).properties(
    width = 600,
    height= 500,
    title = "Monto adjudicado por proveedor (Top 20)"
)

contratos_proveedor | monto_proveedor

alt.HConcatChart(...)

In [ ]:
#Monto gastado por objeto de contrato (top 20)

monto_objeto = alt.Chart(df).mark_bar().encode(
    x = alt.X('sum(monto_contrato_minimo):Q', title = "Monto adjudicado"),
    y = alt.Y('objeto_contrato:N', sort='-x', title = "Objeto de contrato"),
).transform_window(
  rank='rank(monto_contrato_minimo))',
  sort=[alt.SortField('monto_contrato_minimo', order='descending')]
).transform_filter(
  alt.datum.rank <= 23
).properties(
    width = 600,
    height= 500,
    title = "Monto adjudicado por objeto de contrato (Top 20)"
)

# Número de contratos asignados por objetos de contrato (Top 20) 

num_objeto = alt.Chart(df).mark_bar().encode(
  x = alt.X('count:Q', title = "Número de contratos"),
  y = alt.Y('objeto_contrato:N', sort='-x', title = "Objeto de contrato")
).transform_aggregate(
  count='count()',
  groupby=['objeto_contrato']
).transform_window(
  rank='rank(count)',
  sort=[alt.SortField('count', order='descending')]
).transform_filter(
  alt.datum.rank <= 20
).properties(
    width = 600,
    height= 500,
    title = "Número de contratos por objeto de contrato (Top 22)"
)

num_objeto | monto_objeto

alt.HConcatChart(...)

In [ ]:
# Número de contratos emitidos por ente

ente_contratos = alt.Chart(df).mark_bar().encode(
  x = alt.X('count:Q', title = "Número de contratos"),
  y = alt.Y('ente_nombre:N', sort='-x', title = "Ente")
).transform_aggregate(
  count='count()',
  groupby=['ente_nombre']
).transform_window(
  rank='rank(count)',
  sort=[alt.SortField('count', order='descending')]
).transform_filter(
  alt.datum.rank <= 20
).properties(
    width = 600,
    height= 500,
    title = "Número de contratos adjudicados por ente (Top 21)"
)



# Monto total gastado por ente (top 20)

ente_monto = alt.Chart(df).mark_bar().encode(
    x = alt.X('sum(monto_contrato_minimo):Q', title = "Monto adjudicado"),
    y = alt.Y('ente_nombre:N', sort='-x', title = "Ente")
).transform_window(
  rank='rank(monto_contrato_minimo))',
  sort=[alt.SortField('monto_contrato_minimo', order='descending')]
).transform_filter(
  alt.datum.rank <= 125
).properties(
    width = 600,
    height= 500,
    title = "Monto adjudicado por ente (Top 21)"
)

ente_contratos | ente_monto

alt.HConcatChart(...)

In [ ]:
# Número de contratos por tipo
tipo_contratos = alt.Chart(df).mark_bar().encode(
  x = alt.X('count:Q', title = "Número de contratos"),
  y = alt.Y('tipo_contrato:N', sort='-x', title = "Tipo de contrato")
).transform_aggregate(
  count='count()',
  groupby=['tipo_contrato']
).transform_window(
  rank='rank(count)',
  sort=[alt.SortField('count', order='descending')]
).transform_filter(
  alt.datum.rank <= 10
).properties(
    width = 600,
    height= 100,
    title = "Número de contratos asignados por tipo de contrato"
)



# Monto total gastado tipo de contrato

tipo_contrato_monto = alt.Chart(df).mark_bar().encode(
    x = alt.X('sum(monto_contrato_minimo):Q', title = "Monto adjudicado"),
    y = alt.Y('tipo_contrato:N', sort='-x', title = "Tipo de contrato")
).transform_window(
  rank='rank(monto_contrato_minimo))',
  sort=[alt.SortField('monto_contrato_minimo', order='descending')]
).transform_filter(
  alt.datum.rank <= 50
).properties(
    width = 600,
    height= 100,
    title = "Monto total adjudicado por tipo de contrato"
)

tipo_contratos |  tipo_contrato_monto

alt.HConcatChart(...)

In [ ]:

# número de cotizaciones por contrato
no_cotizaciones = alt.Chart(df).mark_bar().encode(
  x = alt.X('count:Q', title = "Número de contratos"),
  y = alt.Y('no_cotizaciones:N', sort='-x', title = "Número de cotizaciones viables")
).transform_aggregate(
  count='count()',
  groupby=['no_cotizaciones']
).transform_window(
  rank='rank(count)',
  sort=[alt.SortField('count', order='descending')]
).transform_filter(
  alt.datum.rank <= 100
).properties(
    width = 1000,
    height= 200,
    title = "Número de cotizaciones viables por contrato previo a la adjudicación"
)

no_cotizaciones


alt.Chart(...)

# **Principales Hallazgos**
-------
### Proveedores
- Si bien la **_Comercializadora Tecno-hospitalaria SA de CV_**, es la empresa que mayor número de contratos ha recibido, con **53** y un **6.8%** del total hasta la fecha (11/10/2020), **no figura en el top 20 de proveedores que mayor monto han recibido**.

- Respecto al proveedor que más dinero ha recibido a la fecha, destaca **_Adriana Guillermina Bussey_** con más de **90 Millones de pesos** adjudicados a la fecha. Este proveedor **no figura en el Top 20 de número de contratos por proveedor**. 

### Insumos adquiridos
- Lo que más se ha adquirido hasta la fecha ,tomando como referencia el *Objeto de Contrato*, es **gel antibacterial** (15% del total de los contratos).
- En lo que más se ha gastado, es en la **_Adquisición de ropa desechable_**. Poco más de **125 millones de pesos.**

### Tipos de contrato
- **52.4%** de los contratos fueron adjudicados en formato **_abierto_**, seguido por un **46.9%** con un formato **_cerrado_**. Sin embargo, casi **600 millones de pesos** fueron adjudicados en el formato **_cerrado_**, mientras que en el formato **_abierto_** poco más de **100 millones de pesos**. 

### Contratos por fecha
- El **27 de marzo** fue el día que **más contratos se han adjudicado a la fecha** (11/10/2020). Dicho día, se adjudicó el **9.2%** (72) de los contratos.

### Tipo de contrato
- El **94% de los contratos** fueron adjudicados para la **adquisición de bienes**, seguido por un **5.5%** para la **prestación de servicios** y **0.5%** para el **arrendamiento de bienes**. 

### Competencia
- El **37.4%** de los **contratos adjudicados**, contaron con hasta **4 propuestas viables** previo a la adjudicación. Le sigue procesos de contratación con hasta **3 propuestas viables** por procesos de adjudicación, que corresponden el **14.9%** total.
- Sólo **8.5%** de los procesos de adjudicación contaron con **sólo una propuesta viable**. 


# Refencias
------------
- [Pandas count and percentage by value for a column](https://blog.softhints.com/pandas-count-percentage-value-column/)
- [How can I order or filter hierarchically this plot from Altair?](https://stackoverflow.com/questions/64285777/how-can-i-order-or-filter-hierarchically-this-plot-from-altair)
- [It is possible to filter and plot it in a descending from sum X on Altair?](https://stackoverflow.com/questions/64295049/it-is-possible-to-filter-and-plot-it-in-a-descending-from-sum-x-on-altair)
- [Contratos adjudicados por COVID-19 - Datos Abiertos de la Ciudad de México](https://datos.cdmx.gob.mx/explore/dataset/contratos-adjudicados-covid19/table/)

